In [1]:
import pandas as pd

# Cargar product_id_apredecir201912.txt
df_ids = pd.read_csv('product_id_apredecir201912.txt')
df_ids.head()

product_id
0       20001
1       20002
2       20003
3       20004
4       20005

In [2]:
# Cargar sell-in.txt (puede ser un archivo grande, leer solo columnas necesarias)
sellin_cols = ['periodo', 'customer_id', 'product_id', 'plan_precios_cuidados', 'cust_request_qty', 'cust_request_tn', 'tn']
df_sellin = pd.read_csv('sell-in.txt', sep='\t', usecols=sellin_cols)
df_sellin.head()

periodo  customer_id  product_id  plan_precios_cuidados  cust_request_qty  \
0   201701        10234       20524                      0                 2   
1   201701        10032       20524                      0                 1   
2   201701        10217       20524                      0                 1   
3   201701        10125       20524                      0                 1   
4   201701        10012       20524                      0                11   

   cust_request_tn       tn  
0          0.05300  0.05300  
1          0.13628  0.13628  
2          0.03028  0.03028  
3          0.02271  0.02271  
4          1.54452  1.54452

In [3]:
# Contar valores únicos de customer_id
df_sellin['customer_id'].nunique()
# Contar valores únicos de product_id
#df_sellin['product_id'].nunique()
# Contar valores únicos de periodo
#df_sellin['periodo'].nunique()


597

In [4]:
# Merge de ambos dataframes por product_id
#df_merged = pd.merge(df_sellin, df_ids, on='product_id', how='inner')
#df_merged.head()

In [5]:
# Si 'periodo' es tipo string o int, conviértelo a datetime para mayor facilidad
df_sellin['periodo'] = pd.to_datetime(df_sellin['periodo'], format='%Y%m')
df_sellin= df_sellin.sort_values(['product_id', 'customer_id', 'periodo']).reset_index(drop=True)


Hacer el producto cartesiano de producto-cliente-período y agregar 0s.

In [6]:
# 1. Listas de valores únicos
product_ids = df_sellin['product_id'].unique()
customer_ids = df_sellin['customer_id'].unique()
periodos = pd.date_range(
    start=df_sellin['periodo'].min(), 
    end=df_sellin['periodo'].max(), 
    freq='MS'  # Monthly start frequency
)

# 2. Producto cartesiano
cartesian = pd.MultiIndex.from_product(
    [product_ids, customer_ids, periodos], 
    names=['product_id', 'customer_id', 'periodo']
).to_frame(index=False)

In [7]:
# 3. Filtrar productos activos
periodo_producto = df_sellin.groupby('product_id')['periodo'].agg(['min', 'max']).reset_index()
periodo_producto.columns = ['product_id', 'periodo_min_producto', 'periodo_max_producto']

# 4. Filtrar clientes activos
periodo_customer = df_sellin.groupby('customer_id')['periodo'].agg(['min', 'max']).reset_index()
periodo_customer.columns = ['customer_id', 'periodo_min_customer', 'periodo_max_customer']

In [8]:
# 5. Merge para filtrar combinaciones válidas
cartesian = cartesian.merge(periodo_producto, on='product_id', how='left')
cartesian = cartesian.merge(periodo_customer, on='customer_id', how='left')

# 6. Filtrar combinaciones donde el periodo esté dentro del rango activo
cartesian = cartesian[
    (cartesian['periodo'] >= cartesian['periodo_min_producto']) & 
    (cartesian['periodo'] <= cartesian['periodo_max_producto']) &
    (cartesian['periodo'] >= cartesian['periodo_min_customer']) #&
    #(cartesian['periodo'] <= cartesian['periodo_max_customer'])
].copy()

# 7. Merge con el dataset original
df_final = cartesian.merge(
    df_sellin, 
    on=['product_id', 'customer_id', 'periodo'], 
    how='left'
)

In [9]:
df_final.shape

(17173448, 11)

In [10]:
# 8. Completar las ventas y cualquier otra variable faltante con 0
df_final['tn'] = df_final['tn'].fillna(0)
df_final['plan_precios_cuidados'] = df_final['plan_precios_cuidados'].fillna(0)
df_final['cust_request_qty'] = df_final['cust_request_qty'].fillna(0)
df_final['cust_request_tn'] = df_final['cust_request_tn'].fillna(0)
# Podés extender esto a otras variables que consideres relevantes.

# 9. Revisar el resultado
print(df_final.head())

   product_id  customer_id    periodo periodo_min_producto  \
0       20001        10001 2017-01-01           2017-01-01   
1       20001        10001 2017-02-01           2017-01-01   
2       20001        10001 2017-03-01           2017-01-01   
3       20001        10001 2017-04-01           2017-01-01   
4       20001        10001 2017-05-01           2017-01-01   

  periodo_max_producto periodo_min_customer periodo_max_customer  \
0           2019-12-01           2017-01-01           2019-12-01   
1           2019-12-01           2017-01-01           2019-12-01   
2           2019-12-01           2017-01-01           2019-12-01   
3           2019-12-01           2017-01-01           2019-12-01   
4           2019-12-01           2017-01-01           2019-12-01   

   plan_precios_cuidados  cust_request_qty  cust_request_tn         tn  
0                    0.0              11.0         99.43861   99.43861  
1                    0.0              23.0        198.84365  198.84365  

Creación de variable target: tn_t_plus_2

In [11]:
# Creamos la variable objetivo: tn en t+2 para cada combinación product_id y customer_id
# df_merged['tn_t_plus_2']

# Paso 1: Crear columna con periodo +2 meses
df_final['periodo_target'] = df_final['periodo'] + pd.DateOffset(months=2)

# Paso 2: Crear DataFrame con target
target_df = df_final[['product_id', 'customer_id', 'periodo', 'tn']].copy()
target_df.rename(columns={'periodo': 'periodo_target', 'tn': 'tn_t_plus_2'}, inplace=True)

# Paso 3: Hacer el merge
df_final = df_final.merge(
    target_df,
    on=['product_id', 'customer_id', 'periodo_target'],
    how='left'
)

# Paso 4: Validar
print(df_final[['product_id', 'customer_id', 'periodo', 'tn', 'tn_t_plus_2']].head(20))




    product_id  customer_id    periodo         tn  tn_t_plus_2
0        20001        10001 2017-01-01   99.43861     92.46537
1        20001        10001 2017-02-01  198.84365     13.29728
2        20001        10001 2017-03-01   92.46537    101.00563
3        20001        10001 2017-04-01   13.29728    128.04792
4        20001        10001 2017-05-01  101.00563    101.20711
5        20001        10001 2017-06-01  128.04792     43.33930
6        20001        10001 2017-07-01  101.20711    289.35024
7        20001        10001 2017-08-01   43.33930    222.11389
8        20001        10001 2017-09-01  289.35024    111.54944
9        20001        10001 2017-10-01  222.11389    131.27150
10       20001        10001 2017-11-01  111.54944     49.61857
11       20001        10001 2017-12-01  131.27150     88.44065
12       20001        10001 2018-01-01   49.61857    214.72336
13       20001        10001 2018-02-01   88.44065    132.83419
14       20001        10001 2018-03-01  214.72336    16

In [12]:
# Eliminamos filas donde no hay target (NaN)
#df_model = df_merged.dropna(subset=['tn_t_plus_2'])

In [13]:
# Probar combinaciones de producto - cliente
df_final[(df_final['product_id'] == 20524) & (df_final['customer_id'] == 10125)].head(10)

product_id  customer_id    periodo periodo_min_producto  \
8959408       20524        10125 2017-01-01           2017-01-01   
8959409       20524        10125 2017-02-01           2017-01-01   
8959410       20524        10125 2017-03-01           2017-01-01   
8959411       20524        10125 2017-04-01           2017-01-01   
8959412       20524        10125 2017-05-01           2017-01-01   
8959413       20524        10125 2017-06-01           2017-01-01   
8959414       20524        10125 2017-07-01           2017-01-01   
8959415       20524        10125 2017-08-01           2017-01-01   
8959416       20524        10125 2017-09-01           2017-01-01   
8959417       20524        10125 2017-10-01           2017-01-01   

        periodo_max_producto periodo_min_customer periodo_max_customer  \
8959408           2019-12-01           2017-01-01           2019-11-01   
8959409           2019-12-01           2017-01-01           2019-11-01   
8959410           2019-12-01           2017-01-01           2019-11-01   
8959411           2019-12-01           2017-01-01           2019-11-01   
8959412           2019-12-01           2017-01-01           2019-11-01   
8959413           2019-12-01           2017-01-01           2019-11-01   
8959414           2019-12-01           2017-01-01           2019-11-01   
8959415           2019-12-01           2017-01-01           2019-11-01   
8959416           2019-12-01           2017-01-01           2019-11-01   
8959417           2019-12-01           2017-01-01           2019-11-01   

         plan_precios_cuidados  cust_request_qty  cust_request_tn       tn  \
8959408                    0.0               1.0          0.02271  0.02271   
8959409                    0.0               0.0          0.00000  0.00000   
8959410                    0.0               0.0          0.00000  0.00000   
8959411                    0.0               1.0          0.00757  0.00757   
8959412                    0.0               1.0          0.00757  0.00757   
8959413                    0.0               0.0          0.00000  0.00000   
8959414                    0.0               0.0          0.00000  0.00000   
8959415                    0.0               0.0          0.00000  0.00000   
8959416                    0.0               1.0          0.00757  0.00757   
8959417                    0.0               1.0          0.00757  0.00757   

        periodo_target  tn_t_plus_2  
8959408     2017-03-01      0.00000  
8959409     2017-04-01      0.00757  
8959410     2017-05-01      0.00757  
8959411     2017-06-01      0.00000  
8959412     2017-07-01      0.00000  
8959413     2017-08-01      0.00000  
8959414     2017-09-01      0.00757  
8959415     2017-10-01      0.00757  
8959416     2017-11-01      0.00000  
8959417     2017-12-01      0.00000

Feature engeneering

In [14]:
df_full = df_final.copy()

# Elimino columnas innecesarias
df_full.drop(columns=['periodo_min_producto', 'periodo_max_producto', 'periodo_min_customer', 'periodo_max_customer', 'periodo_target'], inplace=True)
df_full.head()

product_id  customer_id    periodo  plan_precios_cuidados  \
0       20001        10001 2017-01-01                    0.0   
1       20001        10001 2017-02-01                    0.0   
2       20001        10001 2017-03-01                    0.0   
3       20001        10001 2017-04-01                    0.0   
4       20001        10001 2017-05-01                    0.0   

   cust_request_qty  cust_request_tn         tn  tn_t_plus_2  
0              11.0         99.43861   99.43861     92.46537  
1              23.0        198.84365  198.84365     13.29728  
2              33.0         92.46537   92.46537    101.00563  
3               8.0         13.29728   13.29728    128.04792  
4              15.0        101.20711  101.00563    101.20711

In [15]:
df_full.shape

(17173448, 8)

1. Lags (valores previos)


In [16]:
for lag in range(1, 37):
    df_full[f'tn_lag_{lag}'] = df_full.groupby(['product_id', 'customer_id'])['tn'].shift(lag)

2. Rolling Mean (media móvil)
media de los últimos 3, 6, 9 y 12 meses:

In [17]:
for window in [3, 6, 9, 12, 15, 18, 21, 24]:  #15, 18, 21, 24
    df_full[f'tn_rollmean_{window}'] = (
        df_full.groupby(['product_id', 'customer_id'])['tn']
        .transform(lambda x: x.rolling(window, min_periods=1).mean())
    )

3. Rolling Sum (suma móvil)
la suma de los últimos 3 meses:

In [18]:
df_full['tn_rollsum_3'] = (
    df_full.groupby(['product_id', 'customer_id'])['tn']
    .transform(lambda x: x.rolling(3, min_periods=1).sum())
)

4. Promedio histórico por producto y cliente
Capturar el comportamiento típico de cada combinación:

In [19]:
# Promedio histórico de tn por product_id y customer_id hasta el periodo actual (excluyendo el actual)
df_full['tn_mean_hist'] = (
    df_full.groupby(['product_id', 'customer_id'])['tn']
    .transform(lambda x: x.expanding().mean().shift(1))
)

5. Lag y rolling para otras variables
Repetir la lógica para otras columnas como cust_request_qty y cust_request_tn:

In [20]:
for col in ['cust_request_qty', 'cust_request_tn']:
    for lag in [1, 2, 3]:
        df_full[f'{col}_lag_{lag}'] = df_full.groupby(['product_id', 'customer_id'])[col].shift(lag)
    
    for window in [3, 6, 12]:
        df_full[f'{col}_rollmean_{window}'] = (
            df_full.groupby(['product_id', 'customer_id'])[col]
            .transform(lambda x: x.rolling(window, min_periods=1).mean())
        )

6. Diferencias respecto a valores pasados

In [21]:
for lag in [1, 2, 3, 6]:
    df_full[f'tn_diff_lag_{lag}'] = (
        df_full.groupby(['product_id', 'customer_id'])['tn']
        .transform(lambda x: x - x.shift(lag))
    )


7. Diferencias respecto a rolling mean

In [22]:
for window in [3, 6, 9, 12]:
    rm_col = f'tn_rollmean_{window}'
    df_full[f'tn_diff_rm_{window}'] = df_full['tn'] - df_full[rm_col]


8. Ratios respecto a rolling mean

In [23]:
for window in [3, 6, 9, 12]:
    rm_col = f'tn_rollmean_{window}'
    df_full[f'tn_ratio_rm_{window}'] = df_full['tn'] / (df_full[rm_col] + 0.1)  # evita división por cero


9. Indicadores binarios

In [24]:
df_full['tn_is_increasing'] = (
    df_full.groupby(['product_id', 'customer_id'])['tn']
    .transform(lambda x: (x > x.shift(1)).astype(int))
)

for window in [3, 6]:
    rm_col = f'tn_rollmean_{window}'
    df_full[f'tn_above_rm_{window}'] = (df_full['tn'] > df_full[rm_col]).astype(int)


10. Volatilidad local (qué tan variable es el valor en una ventana)

In [25]:
for window in [3, 6, 12]:
    df_full[f'tn_volatility_{window}'] = (
        df_full.groupby(['product_id', 'customer_id'])['tn']
        .transform(lambda x: x.rolling(window).std())
    )

11. Ratio contra t-1 o rolling anterior (más versiones)

In [26]:
for lag in [1, 2, 3]:
    df_full[f'tn_ratio_lag_{lag}'] = df_full['tn'] / (df_full.groupby(['product_id', 'customer_id'])['tn'].shift(lag) + 0.1)


12. Contadores de inactividad o explosión (períodos que pasaron sin ventas / períodos con crecimiento fuerte)

In [27]:
df_full['tn_zero'] = (df_full['tn'] == 0).astype(int)

for window in [3, 6, 12]:
    df_full[f'tn_zero_count_{window}'] = (
        df_full.groupby(['product_id', 'customer_id'])['tn_zero']
        .transform(lambda x: x.rolling(window, min_periods=1).sum())
    )



13. Features categóricos de comportamiento (Agrupar por cuartiles)

In [29]:
import numpy as np

df_full['tn_quantile'] = (
    df_full.groupby(['product_id', 'customer_id'])['tn']
    .transform(lambda x: pd.qcut(
        x.rank(method='first') if x.nunique() >= 4 else pd.Series([np.nan]*len(x), index=x.index),
        4,
        labels=False,
        duplicates='drop'
    ))
)


14. Features temporales (mes, estacionalidad)

In [30]:
import numpy as np

df_full['month'] = df_full['periodo'].dt.month
df_full['quarter'] = df_full['periodo'].dt.quarter
df_full['year'] = df_full['periodo'].dt.year
df_full['month_sin'] = np.sin(2 * np.pi * df_full['month'] / 12)
df_full['month_cos'] = np.cos(2 * np.pi * df_full['month'] / 12)


In [31]:
# Probar combinaciones de producto - cliente
#df_full[(df_full['product_id'] == 20524) & (df_final['customer_id'] == 10125)].head(10)
df_full.head()

product_id  customer_id    periodo  plan_precios_cuidados  \
0       20001        10001 2017-01-01                    0.0   
1       20001        10001 2017-02-01                    0.0   
2       20001        10001 2017-03-01                    0.0   
3       20001        10001 2017-04-01                    0.0   
4       20001        10001 2017-05-01                    0.0   

   cust_request_qty  cust_request_tn         tn  tn_t_plus_2   tn_lag_1  \
0              11.0         99.43861   99.43861     92.46537        NaN   
1              23.0        198.84365  198.84365     13.29728   99.43861   
2              33.0         92.46537   92.46537    101.00563  198.84365   
3               8.0         13.29728   13.29728    128.04792   92.46537   
4              15.0        101.20711  101.00563    101.20711   13.29728   

    tn_lag_2  ...  tn_zero  tn_zero_count_3  tn_zero_count_6  \
0        NaN  ...        0              0.0              0.0   
1        NaN  ...        0              0.0              0.0   
2   99.43861  ...        0              0.0              0.0   
3  198.84365  ...        0              0.0              0.0   
4   92.46537  ...        0              0.0              0.0   

   tn_zero_count_12  tn_quantile  month  quarter  year  month_sin  \
0               0.0          0.0      1        1  2017   0.500000   
1               0.0          2.0      2        1  2017   0.866025   
2               0.0          0.0      3        1  2017   1.000000   
3               0.0          0.0      4        2  2017   0.866025   
4               0.0          1.0      5        2  2017   0.500000   

      month_cos  
0  8.660254e-01  
1  5.000000e-01  
2  6.123234e-17  
3 -5.000000e-01  
4 -8.660254e-01  

[5 rows x 97 columns]

In [49]:
# Guardar el DataFrame final
df_full.to_parquet("df_full.parquet")

---

#### Identificar clientes importantes

In [32]:
# Consistencia: cuántos meses tiene ventas
ventas_mensuales = df_full[df_full['tn'] > 0].groupby('customer_id')['periodo'].nunique()

# Volumen: total de toneladas vendidas
ventas_totales = df_full.groupby('customer_id')['tn'].sum()

# Unir criterios
clientes_importantes = ventas_mensuales[(ventas_mensuales >= 30)]\
    .index.intersection(ventas_totales[ventas_totales >= 10000].index)
print(clientes_importantes)
#clientes_importantes = set(clientes_importantes)


Index([10001, 10002, 10003, 10004, 10005, 10006, 10007, 10008, 10009, 10010,
       10011, 10012, 10013, 10014, 10015, 10016, 10017, 10018, 10019, 10020,
       10021, 10022, 10023, 10024, 10025, 10026],
      dtype='int64', name='customer_id')


In [33]:
# Asignar grupo de cliente
df_full['grupo_cliente'] = df_full['customer_id'].apply(lambda x: 'top' if x in clientes_importantes else 'resto')

---

## Entrenamiento del modelo Light GBM

Preparar los datos de entrenamiento y test
Entrenamiento: Usa todos los datos donde tn_t_plus_2 no es NaN y el período es menor a 201912 (para no usar datos del futuro).
Test: Filtra las filas donde el período es 201912 (diciembre 2019), ya que para esas filas queremos predecir tn en 202002 (febrero 2020).

In [34]:
# Lista de features: incluye todas las columnas que empiezan con los prefijos de los features
feature_cols = [
    col for col in df_full.columns
    if (
        col.startswith('tn_') or
        col.startswith('cust_request_qty_lag_') or
        col.startswith('cust_request_qty_roll') or
        col.startswith('cust_request_tn_lag_') or
        col.startswith('cust_request_tn_roll') or
        col == 'plan_precios_cuidados'  or
        #col == 'product_id' or
        col in ['month', 'quarter', 'year', 'month_sin', 'month_cos']  
    )
]

# Quito la columna 	tn_t_plus_2 de las features
feature_cols = [col for col in feature_cols if col != 'tn_t_plus_2']

In [ ]:
# Verifico los valores de product_id = 20001 y customer_id = 10063
# train[(train['product_id'] == 20001) & (train['customer_id'] == 10063) & (train['periodo'] > pd.to_datetime('2019-01-01'))]
#df_full[(df_full['product_id'] == 20064) & (df_full['customer_id'] == 10001) & (df_full['periodo'] > pd.to_datetime('2019-01-01'))]

#### Modelo jerárquico

In [35]:
# Separar datasets
filtro_clientes_top = df_full["customer_id"].isin(clientes_importantes)
df_full_cliente = df_full[filtro_clientes_top].copy()
df_full_rest = df_full[~filtro_clientes_top].copy()


df_full_prod = (
    df_full_rest
    .groupby(['product_id', 'periodo'], as_index=False)
    .agg({**{f: 'sum' for f in feature_cols}, 'tn_t_plus_2': 'sum', 'tn': 'sum'})
)

In [36]:
# Dataset para clientes importantes
train_top = df_full_cliente[(df_full_cliente['periodo'] < '2019-10-01') & df_full_cliente['tn_t_plus_2'].notnull()]
valid_top = df_full_cliente[(df_full_cliente['periodo'] == '2019-10-01') & df_full_cliente['tn_t_plus_2'].notnull()]

# Dataset para el resto de los clientes
train_resto = df_full_prod[(df_full_prod['periodo'] < '2019-10-01') & df_full_prod['tn_t_plus_2'].notnull()]
valid_resto = df_full_prod[(df_full_prod['periodo'] == '2019-10-01') & df_full_prod['tn_t_plus_2'].notnull()]


In [ ]:
'''# Entrenamiento y validación
train = df_full[df_full['periodo'] < pd.to_datetime('2019-10-01')]
train = train[train['tn_t_plus_2'].notnull()] # Filtro con target válido
valid = df_full[df_full['periodo'] == pd.to_datetime('2019-10-01')]
valid = valid[valid['tn_t_plus_2'].notnull()] # Filtro con target válido
test = df_full[df_full['periodo'] == pd.to_datetime('2019-12-01')]

X_train = train[feature_cols]
y_train = train['tn_t_plus_2']
X_valid = valid[feature_cols]
y_valid = valid['tn_t_plus_2']
X_test = test[feature_cols]

# Sample weights basados en tn (reemplazando 0 por 0.1)
train_weights = train['tn'].clip(lower=0.1)
valid_weights = valid['tn'].clip(lower=0.1)'''

"# Entrenamiento y validación\ntrain = df_full[df_full['periodo'] < pd.to_datetime('2019-10-01')]\ntrain = train[train['tn_t_plus_2'].notnull()] # Filtro con target válido\nvalid = df_full[df_full['periodo'] == pd.to_datetime('2019-10-01')]\nvalid = valid[valid['tn_t_plus_2'].notnull()] # Filtro con target válido\ntest = df_full[df_full['periodo'] == pd.to_datetime('2019-12-01')]\n\nX_train = train[feature_cols]\ny_train = train['tn_t_plus_2']\nX_valid = valid[feature_cols]\ny_valid = valid['tn_t_plus_2']\nX_test = test[feature_cols]\n\n# Sample weights basados en tn (reemplazando 0 por 0.1)\ntrain_weights = train['tn'].clip(lower=0.1)\nvalid_weights = valid['tn'].clip(lower=0.1)"

In [ ]:
'''# Chequeo de NaNs en y_train y y_valid
print("NaNs en y_train:", y_train.isnull().sum())
print("NaNs en y_valid:", y_valid.isnull().sum())
'''


'# Chequeo de NaNs en y_train y y_valid\nprint("NaNs en y_train:", y_train.isnull().sum())\nprint("NaNs en y_valid:", y_valid.isnull().sum())\n'

In [ ]:
'''invalid_rows = valid[valid['tn_t_plus_2'].isnull()]


productos_con_nan_target = invalid_rows['product_id'].unique()
print("Productos con target nulo:", productos_con_nan_target)'''


'invalid_rows = valid[valid[\'tn_t_plus_2\'].isnull()]\n\n\nproductos_con_nan_target = invalid_rows[\'product_id\'].unique()\nprint("Productos con target nulo:", productos_con_nan_target)'

In [ ]:

'''productos_activos = df_ids['product_id'].unique()
print("Productos activos en 2019-12:", productos_activos)'''


'productos_activos = df_ids[\'product_id\'].unique()\nprint("Productos activos en 2019-12:", productos_activos)'

In [ ]:
'''df_resultado = pd.DataFrame({'product_id': productos_con_nan_target})
df_resultado['activo_en_201912'] = df_resultado['product_id'].isin(productos_activos)
print(df_resultado)'''



"df_resultado = pd.DataFrame({'product_id': productos_con_nan_target})\ndf_resultado['activo_en_201912'] = df_resultado['product_id'].isin(productos_activos)\nprint(df_resultado)"

#### Entrena el modelo LightGBM

In [37]:
# Optimización con Optuna del modelo jerárquico

import numpy as np
import lightgbm as lgb
import optuna



def run_optuna_study(X_train, y_train, X_valid, y_valid, train_weights, valid_weights, study_name):
    def total_forecast_error(y_true, y_pred):
        error_abs = np.abs(y_true - y_pred)
        return np.sum(error_abs) / np.sum(y_true)

    def objective(trial):
        param = {
            'objective': 'regression',
            'metric': 'mse',
            'min_child_weight': trial.suggest_int('min_child_weight', 1, 10),
            'n_estimators': trial.suggest_int('n_estimators', 500, 1000),
            'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
            'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
            'num_leaves': trial.suggest_int('num_leaves', 20, 150),
            'max_depth': trial.suggest_int('max_depth', 3, 20),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
            'linear_tree': True  #
        }

        model = lgb.LGBMRegressor(**param)
        model.fit(
            X_train, y_train,
            sample_weight=train_weights,
            eval_set=[(X_valid, y_valid)],
            eval_sample_weight=[valid_weights]
        )

        y_pred = model.predict(X_valid)
        return total_forecast_error(y_valid, y_pred)

    storage = optuna.storages.RDBStorage(url="sqlite:///optuna_study.db")
    study = optuna.create_study(
        study_name=study_name,
        direction='minimize',
        storage=storage,
        load_if_exists=True
    )
    study.optimize(objective, n_trials=100)
    
    print(f"Study '{study_name}' - Best params:", study.best_params)
    print(f"Study '{study_name}' - Best TFE:", study.best_value)

    
    return study


In [38]:
# Corro la optimización para el dataset de clientes importantes

# Para modelo de clientes importantes (producto-cliente)
X_train_cliente = train_top[feature_cols]
y_train_cliente = train_top['tn_t_plus_2']
X_valid_cliente = valid_top[feature_cols]
y_valid_cliente = valid_top['tn_t_plus_2']

# Sample weight con clip en 0.1
train_weights_cliente = train_top['tn'].clip(lower=0.1)
valid_weights_cliente = valid_top['tn'].clip(lower=0.1)


study_cliente = run_optuna_study(
    X_train_cliente, y_train_cliente,
    X_valid_cliente, y_valid_cliente,
    train_weights_cliente, valid_weights_cliente,
    study_name="tuning_cliente4"
)


[I 2025-07-13 16:11:05,181] Using an existing study with name 'tuning_cliente4' instead of creating a new one.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.024560 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 17808
[LightGBM] [Info] Number of data points in the train set: 731978, number of used features: 86
[LightGBM] [Info] Start training from score 20.665763
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-07-13 16:11:21,126] Trial 460 finished with value: 0.9495750123302845 and parameters: {'min_child_weight': 1, 'n_estimators': 527, 'reg_alpha': 0.9009535892566571, 'reg_lambda': 0.9469488925774119, 'learning_rate': 0.010031053895040784, 'num_leaves': 150, 'max_depth': 7, 'subsample': 0.6238375821881705, 'colsample_bytree': 0.5267940360555632}. Best is trial 450 with value: 0.8889364304794785.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.026534 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 17808
[LightGBM] [Info] Number of data points in the train set: 731978, number of used features: 86
[LightGBM] [Info] Start training from score 20.665763
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-07-13 16:11:39,957] Trial 461 finished with value: 0.9769753894517236 and parameters: {'min_child_weight': 5, 'n_estimators': 536, 'reg_alpha': 0.6520371679203001, 'reg_lambda': 0.3296835979335798, 'learning_rate': 0.01189385128010904, 'num_leaves': 142, 'max_depth': 8, 'subsample': 0.8305350584582916, 'colsample_bytree': 0.5171639772806511}. Best is trial 450 with value: 0.8889364304794785.


...

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.020606 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 17808
[LightGBM] [Info] Number of data points in the train set: 731978, number of used features: 86
[LightGBM] [Info] Start training from score 20.665763
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-07-13 16:43:44,800] Trial 558 finished with value: 1.0243436184881283 and parameters: {'min_child_weight': 3, 'n_estimators': 728, 'reg_alpha': 0.8643906060615774, 'reg_lambda': 0.25797063239420726, 'learning_rate': 0.01060973093496013, 'num_leaves': 146, 'max_depth': 7, 'subsample': 0.52173201944228, 'colsample_bytree': 0.5094192548260373}. Best is trial 450 with value: 0.8889364304794785.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.020710 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 17808
[LightGBM] [Info] Number of data points in the train set: 731978, number of used features: 86
[LightGBM] [Info] Start training from score 20.665763
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-07-13 16:44:09,479] Trial 559 finished with value: 1.0277404467244484 and parameters: {'min_child_weight': 5, 'n_estimators': 616, 'reg_alpha': 0.6044308633509735, 'reg_lambda': 0.42769298290836555, 'learning_rate': 0.013423201432403543, 'num_leaves': 136, 'max_depth': 8, 'subsample': 0.6051421992795923, 'colsample_bytree': 0.5562271387477472}. Best is trial 450 with value: 0.8889364304794785.


Study 'tuning_cliente4' - Best params: {'min_child_weight': 5, 'n_estimators': 540, 'reg_alpha': 0.6228452031279299, 'reg_lambda': 0.8732126454352676, 'learning_rate': 0.011164746626431713, 'num_leaves': 144, 'max_depth': 7, 'subsample': 0.5517042316607734, 'colsample_bytree': 0.5271816306436891}
Study 'tuning_cliente4' - Best TFE: 0.8889364304794785


In [39]:
# Corro la optimización para el dataset del resto de los clientes

# Para modelo del resto (nivel producto)
X_train_prod = train_resto[feature_cols]
y_train_prod = train_resto['tn_t_plus_2']
X_valid_prod = valid_resto[feature_cols]
y_valid_prod = valid_resto['tn_t_plus_2']

# Sample weight con clip en 0.1
train_weights_prod = train_resto['tn'].clip(lower=0.1)
valid_weights_prod = valid_resto['tn'].clip(lower=0.1)


study_resto = run_optuna_study(
    X_train_prod, y_train_prod,
    X_valid_prod, y_valid_prod,
    train_weights_prod, valid_weights_prod,
    study_name="tuning_prod4"
)


[I 2025-07-13 16:44:09,515] Using an existing study with name 'tuning_prod4' instead of creating a new one.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003760 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 20394
[LightGBM] [Info] Number of data points in the train set: 28697, number of used features: 86
[LightGBM] [Info] Start training from score 91.409881
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gai

[I 2025-07-13 16:44:11,062] Trial 450 finished with value: 0.38866931793616877 and parameters: {'min_child_weight': 3, 'n_estimators': 609, 'reg_alpha': 0.9465940156214567, 'reg_lambda': 0.06273634198252623, 'learning_rate': 0.01262336501407426, 'num_leaves': 26, 'max_depth': 3, 'subsample': 0.6826533770066472, 'colsample_bytree': 0.7741408320335375}. Best is trial 377 with value: 0.3720981565503088.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001947 secon

[I 2025-07-13 16:44:12,193] Trial 451 finished with value: 0.38286762626382814 and parameters: {'min_child_weight': 3, 'n_estimators': 585, 'reg_alpha': 0.9796803668211234, 'reg_lambda': 0.02161191108747669, 'learning_rate': 0.01119240337695285, 'num_leaves': 30, 'max_depth': 3, 'subsample': 0.6909549438467669, 'colsample_bytree': 0.7597013963552905}. Best is trial 377 with value: 0.3720981565503088.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007502 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 20394
[LightGBM] [Info] Number of data points in the train set: 28697, number of used features: 86
[LightGBM] [Info] Start training from score 91.409881
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gai

[I 2025-07-13 16:47:00,852] Trial 548 finished with value: 0.5983231868590823 and parameters: {'min_child_weight': 3, 'n_estimators': 642, 'reg_alpha': 0.9816985670243916, 'reg_lambda': 0.00014871056761096152, 'learning_rate': 0.060305658888305295, 'num_leaves': 37, 'max_depth': 3, 'subsample': 0.7506178423136948, 'colsample_bytree': 0.7746376479425595}. Best is trial 377 with value: 0.3720981565503088.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2025-07-13 16:47:02,240] Trial 549 finished with value: 0.3935295833081796 and parameters: {'min_child_weight': 4, 'n_estimators': 627, 'reg_alpha': 0.9361027833804296, 'reg_lambda': 0.042140799795175224, 'learning_rate': 0.011475571971793577, 'num_leaves': 30, 'max_depth': 3, 'subsample': 0.7767350209995458, 'colsample_bytree': 0.8000192184260148}. Best is trial 377 with value: 0.3720981565503088.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

In [ ]:
# Optuna para optimización de hiperparámetros (no corro por ahora, modificar para el modelo jerárquico)

'''import numpy as np
import lightgbm as lgb
import optuna


storage = optuna.storages.RDBStorage(
    url="sqlite:///optuna_study.db"
)

def total_forecast_error(y_true, y_pred):
    error_abs = np.abs(y_true - y_pred)
    return np.sum(error_abs) / np.sum(y_true)

def objective(trial):
    param = {
        'objective': 'regression',
        'metric': 'mse', 
        'n_estimators': 1000,
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.2, log=True),
        'num_leaves': trial.suggest_int('num_leaves', 20, 150),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0)
    }

    model = lgb.LGBMRegressor(**param)
    model.fit(
        X_train, y_train,
        sample_weight=train_weights,
        eval_set=[(X_valid, y_valid)],
        eval_sample_weight=[valid_weights],
        verbose=False

    )

    y_pred = model.predict(X_valid)
    tfe = total_forecast_error(y_valid, y_pred)
    return tfe

study2 = optuna.create_study(study_name="model_tuning",direction='minimize', storage=storage,
    load_if_exists=True)
study2.optimize(objective, n_trials=5)

print("Best params:", study2.best_params)
print("Best Total Forecast Error:", study2.best_value)'''


'import numpy as np\nimport lightgbm as lgb\nimport optuna\n\n\nstorage = optuna.storages.RDBStorage(\n    url="sqlite:///optuna_study.db"\n)\n\ndef total_forecast_error(y_true, y_pred):\n    error_abs = np.abs(y_true - y_pred)\n    return np.sum(error_abs) / np.sum(y_true)\n\ndef objective(trial):\n    param = {\n        \'objective\': \'regression\',\n        \'metric\': \'mse\', \n        \'n_estimators\': 1000,\n        \'learning_rate\': trial.suggest_float(\'learning_rate\', 0.01, 0.2, log=True),\n        \'num_leaves\': trial.suggest_int(\'num_leaves\', 20, 150),\n        \'max_depth\': trial.suggest_int(\'max_depth\', 3, 15),\n        \'subsample\': trial.suggest_float(\'subsample\', 0.5, 1.0),\n        \'colsample_bytree\': trial.suggest_float(\'colsample_bytree\', 0.5, 1.0)\n    }\n\n    model = lgb.LGBMRegressor(**param)\n    model.fit(\n        X_train, y_train,\n        sample_weight=train_weights,\n        eval_set=[(X_valid, y_valid)],\n        eval_sample_weight=[valid_

In [40]:
import optuna.visualization as vis

# Visualizar historial de optimización
vis.plot_optimization_history(study_cliente).show()
vis.plot_optimization_history(study_resto).show()


In [ ]:
# Visualizar importancia de parámetros


#vis.plot_param_importances(study_cliente).show()
#vis.plot_param_importances(study_resto).show()

# Relación entre dos hiperparámetros y el score
#vis.plot_contour(study_cliente).show()
#vis.plot_contour(study_resto).show()

# Distribución de cada hiperparámetro
#vis.plot_parallel_coordinate(study_cliente).show()
#vis.plot_parallel_coordinate(study_resto).show()



#### Entrenamiento del modelo jerárquico

In [41]:
import numpy as np
import lightgbm as lgb

# Obtener los mejores parámetros de cada estudio
best_params_top = study_cliente.best_params
best_params_resto = study_resto.best_params

# Agregar los parámetros fijos
best_params_top.update({
    'objective': 'regression',
    'metric': 'mse',
    'linear_tree': True
})

best_params_resto.update({
    'objective': 'regression',
    'metric': 'mse',
    'linear_tree': True
})


# Clientes importantes
# Unificamos train y valid 
train_top_final = pd.concat([train_top, valid_top])

model_top = lgb.LGBMRegressor(**best_params_top)
model_top.fit(
    train_top_final[feature_cols],
    train_top_final['tn_t_plus_2'],
    sample_weight=train_top_final['tn'].clip(lower=0.1)
)

# Resto de clientes
# Unificamos train y valid para el resto de los clientes
train_resto_final = pd.concat([train_resto, valid_resto])

model_resto = lgb.LGBMRegressor(**best_params_resto)
model_resto.fit(
    train_resto_final[feature_cols],
    train_resto_final['tn_t_plus_2'],
    sample_weight=train_resto_final['tn'].clip(lower=0.1)
)


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.021631 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 18063
[LightGBM] [Info] Number of data points in the train set: 755976, number of used features: 87
[LightGBM] [Info] Start training from score 20.760162
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

LGBMRegressor(colsample_bytree=0.7664133455537941,
              learning_rate=0.011271679751400017, linear_tree=True, max_depth=3,
              metric='mse', min_child_weight=5, n_estimators=597, num_leaves=28,
              objective='regression', reg_alpha=0.9202736795517611,
              reg_lambda=0.03608199415619793, subsample=0.7589680484529573)

In [ ]:
# Entrenamiento final del modelo inicial (opcional, si se desea un modelo único)

'''best_params = study2.best_params
best_params['objective'] = 'regression'
best_params['metric'] = 'mse'
best_params['n_estimators'] = 1000
best_params['linear_tree'] = True

final_model = lgb.LGBMRegressor(**best_params)
final_model.fit(
    pd.concat([X_train, X_valid]), 
    pd.concat([y_train, y_valid]),
    sample_weight=pd.concat([train_weights, valid_weights])
)
'''

"best_params = study2.best_params\nbest_params['objective'] = 'regression'\nbest_params['metric'] = 'mse'\nbest_params['n_estimators'] = 1000\nbest_params['linear_tree'] = True\n\nfinal_model = lgb.LGBMRegressor(**best_params)\nfinal_model.fit(\n    pd.concat([X_train, X_valid]), \n    pd.concat([y_train, y_valid]),\n    sample_weight=pd.concat([train_weights, valid_weights])\n)\n"

#### Verificar el rendimiento del modelo (clientes importantes) en validación

In [42]:
# 1. Subset de validación
valid_cliente = df_full_cliente[df_full_cliente['periodo'] == '2019-10-01'].copy()

# 2. Agregar predicciones
valid_cliente['pred'] = model_top.predict(valid_cliente[feature_cols])

# 3. Agrupar por product_id
df_grouped = valid_cliente.groupby('product_id').agg({
    'tn_t_plus_2': 'sum',
    'pred': 'sum'
}).reset_index()

def total_forecast_error(y_true, y_pred):
        error_abs = np.abs(y_true - y_pred)
        return np.sum(error_abs) / np.sum(y_true)

tfe_prod = total_forecast_error(df_grouped['tn_t_plus_2'], df_grouped['pred'])
print(f"TFE a nivel producto (clientes importantes): {tfe_prod:.4f}")

TFE a nivel producto (clientes importantes): 0.3162


#### Feature importance con Shapley

In [ ]:
#pip install shap

In [ ]:
# No lo tengo en cuenta por el momento

'''import shap

# Explicador para modelos de LightGBM
explainer = shap.TreeExplainer(final_model)
shap_values = explainer.shap_values(X_test)

# Resumen global de importancia (barplot)
shap.summary_plot(shap_values, X_test, plot_type="bar")

# Resumen detallado (beeswarm)
shap.summary_plot(shap_values, X_test)'''

'import shap\n\n# Explicador para modelos de LightGBM\nexplainer = shap.TreeExplainer(final_model)\nshap_values = explainer.shap_values(X_test)\n\n# Resumen global de importancia (barplot)\nshap.summary_plot(shap_values, X_test, plot_type="bar")\n\n# Resumen detallado (beeswarm)\nshap.summary_plot(shap_values, X_test)'

---

#### Predicciones para diciembre 2019 (validación para stacking)

In [ ]:
'''# Predicciones para df_full_cliente (modelo a nivel producto-cliente)

df_pred_cliente_v = valid_top.copy()
df_pred_cliente_v['pred'] = model_top.predict(df_pred_cliente_v[feature_cols])
df_pred_cliente_grouped_v = df_pred_cliente_v.groupby('product_id')['pred'].sum().reset_index()
df_pred_cliente_grouped_v.shape'''

(923, 2)

In [ ]:
'''# Predicciones para df_full_prod (modelo a nivel producto)

df_pred_prod_v = valid_resto.copy()
df_pred_prod_v['pred'] = model_resto.predict(df_pred_prod_v[feature_cols])
df_pred_prod_grouped_v = df_pred_prod_v.groupby('product_id')['pred'].sum().reset_index()
df_pred_prod_grouped_v.shape'''

(955, 2)

In [ ]:
'''# Unir ambas predicciones

df_pred_final_v = pd.concat([df_pred_cliente_grouped_v, df_pred_prod_grouped_v], axis=0)

# Volver a agrupar para sumar predicciones
df_pred_final_v = df_pred_final_v.groupby('product_id', as_index=False)['pred'].sum()
df_pred_final_v.rename(columns={'pred': 'tn'}, inplace=True)
df_pred_final_v.shape'''

(955, 2)

In [ ]:
'''# Exportar a CSV 
df_pred_final_v.to_csv('ridge_val_lgbm.csv', index=False)

# Exporto a CSV datos reales 2019 12
df_real_201912 = df_full[df_full['periodo'] == '2019-12-01'][['product_id', 'tn']]
# Agregar por product_id
df_real_201912 = df_real_201912.groupby('product_id')['tn'].sum().reset_index()
#df_real_201912.shape
df_real_201912.to_csv('ridge_real_201912.csv', index=False)'''

---

#### Predicciones para febrero 2020

In [43]:
# Predicciones para df_full_cliente (modelo a nivel producto-cliente)

df_pred_cliente = df_full_cliente[df_full_cliente['periodo'] == '2019-12-01'].copy()
df_pred_cliente['pred'] = model_top.predict(df_pred_cliente[feature_cols])
df_pred_cliente_grouped = df_pred_cliente.groupby('product_id')['pred'].sum().reset_index()
df_pred_cliente_grouped.head()

product_id         pred
0       20001   707.868918
1       20002  1044.377369
2       20003   505.710722
3       20004   227.857966
4       20005   286.034304

In [44]:
# Predicciones para df_full_prod (modelo a nivel producto)

df_pred_prod = df_full_prod[df_full_prod['periodo'] == '2019-12-01'].copy()
df_pred_prod['pred'] = model_resto.predict(df_pred_prod[feature_cols])
df_pred_prod_grouped = df_pred_prod.groupby('product_id')['pred'].sum().reset_index()
df_pred_prod_grouped.head()

product_id        pred
0       20001  194.978618
1       20002  169.322955
2       20003  167.595196
3       20004  218.568974
4       20005  189.311021

In [45]:
# Unir ambas predicciones

df_pred_final = pd.concat([df_pred_cliente_grouped, df_pred_prod_grouped], axis=0)

# Volver a agrupar para sumar predicciones
df_pred_final = df_pred_final.groupby('product_id', as_index=False)['pred'].sum()
df_pred_final.rename(columns={'pred': 'tn'}, inplace=True)
df_pred_final.head()

product_id           tn
0       20001   902.847536
1       20002  1213.700324
2       20003   673.305919
3       20004   446.426940
4       20005   475.345326

In [ ]:
# Predicciones a partir del modelo inicial

'''test['tn_pred_202002'] = final_model.predict(X_test)'''



"test['tn_pred_202002'] = final_model.predict(X_test)"

#### Comparación del TFE entre modelo jerárquico y modelo de 12 meses

In [46]:
# 1. Promedio de los últimos 12 meses de tn
df_prom12 = df_sellin[(df_sellin['periodo'] >= '2018-12-01') & (df_sellin['periodo'] < '2019-12-01' )].copy()
df_prom12 = df_prom12.groupby(['product_id']).agg({'tn': 'sum'}).reset_index()
# Divido por 12 para obtener el promedio
df_prom12['tn'] = df_prom12['tn'] / 12
# Hago el merge con df_ids
df_prom12 = df_prom12.merge(df_ids, on='product_id', how='inner')
#df_prom12.head()


# 2. Predicción del modelo jerárquico para 2019-12
# Predicciones para df_full_cliente (modelo a nivel producto-cliente)
df_pred_cliente2 = df_full_cliente[df_full_cliente['periodo'] == '2019-10-01'].copy()
df_pred_cliente2['pred'] = model_top.predict(df_pred_cliente2[feature_cols])
df_pred_cliente_grouped2 = df_pred_cliente2.groupby('product_id')['pred'].sum().reset_index()
# Predicciones para df_full_prod (modelo a nivel producto)
df_pred_prod2 = df_full_prod[df_full_prod['periodo'] == '2019-10-01'].copy()
df_pred_prod2['pred'] = model_resto.predict(df_pred_prod2[feature_cols])
df_pred_prod_grouped2 = df_pred_prod2.groupby('product_id')['pred'].sum().reset_index()
# Unir ambas predicciones
df_pred_final2 = pd.concat([df_pred_cliente_grouped2, df_pred_prod_grouped2], axis=0)
df_pred_final2 = df_pred_final2.groupby('product_id', as_index=False)['pred'].sum()
df_jer2 = pd.merge(df_pred_final, df_ids, on='product_id', how='inner')



# 3. Comparo con los resultados en 2019 12 
df_real = df_sellin[(df_sellin['periodo'] == pd.to_datetime('2019-12-01'))]
# Agregar por product_id
df_real = df_real.groupby('product_id')['tn'].sum().reset_index()
df_real = df_real.merge(df_ids, on='product_id', how='inner')
#df_real.head()


# 4. Calculo el Total Forecast Error (TFE) entre las predicciones y los valores reales
tfe_prom12 = total_forecast_error(df_real['tn'], df_prom12['tn'])
tfe_jer2 = total_forecast_error(df_real['tn'], df_jer2['tn'])
print(f"TFE con promedio de los últimos 12 meses: {tfe_prom12:.4f}")
print(f"TFE con predicciones del modelo jerárquico: {tfe_jer2:.4f}")

TFE con promedio de los últimos 12 meses: 0.2870
TFE con predicciones del modelo jerárquico: 0.2464


#### Archivo para Kaggle

In [47]:
# Ensamble
'''
# Cargar promedio ult 12M *0,98
df_prom = pd.read_csv('Prom12M098.csv')
#df_prom.head()
df_prom.shape'''

"\n# Cargar promedio ult 12M *0,98\ndf_prom = pd.read_csv('Prom12M098.csv')\n#df_prom.head()\ndf_prom.shape"

In [48]:
# Archivo a partir de modelo jerárquico

# Merge con dataframe ids por product_id
submission_mj = pd.merge(df_pred_final, df_ids, on='product_id', how='inner')
#submission_mj.head()
#submission_mj.shape

# Filtrar valores negativos de tn y cambiar a 0
submission_mj.loc[submission_mj['tn'] < 0, 'tn'] = 0


# Exportar a CSV 
submission_mj.to_csv('submission_mj.csv', index=False)


In [ ]:
'''# Agregar por product_id
submission_agg = test.groupby('product_id')['tn_pred_202002'].sum().reset_index()

# Renombrar 
submission_agg.rename(columns={'tn_pred_202002': 'tn'}, inplace=True)

# Merge con dataframe ids por product_id
submission_agg2 = pd.merge(submission_agg, df_ids, on='product_id', how='inner')
submission_agg3 = submission_agg2.copy()
#submission_agg2.head()
#submission_agg2.shape

# Hago el promedio para el ensamble
submission_agg3['tn'] = (df_prom['tn'] + submission_agg3['tn']) / 2
#submission_agg2.head()

# Exportar a CSV LightGBM & Ensamble
submission_agg2.to_csv('submission.csv', index=False)
submission_agg3.to_csv('submission_e.csv', index=False)'''

"# Agregar por product_id\nsubmission_agg = test.groupby('product_id')['tn_pred_202002'].sum().reset_index()\n\n# Renombrar \nsubmission_agg.rename(columns={'tn_pred_202002': 'tn'}, inplace=True)\n\n# Merge con dataframe ids por product_id\nsubmission_agg2 = pd.merge(submission_agg, df_ids, on='product_id', how='inner')\nsubmission_agg3 = submission_agg2.copy()\n#submission_agg2.head()\n#submission_agg2.shape\n\n# Hago el promedio para el ensamble\nsubmission_agg3['tn'] = (df_prom['tn'] + submission_agg3['tn']) / 2\n#submission_agg2.head()\n\n# Exportar a CSV LightGBM & Ensamble\nsubmission_agg2.to_csv('submission.csv', index=False)\nsubmission_agg3.to_csv('submission_e.csv', index=False)"

df_full 2019 12 - predicción vs realidad

In [ ]:
'''# df_full 2019 12 - predicción vs realidad

df_real = df_full[(df_full['periodo'] == pd.to_datetime('2019-12-01'))]

# Agregar por product_id
df_real = df_real.groupby('product_id')['tn'].sum().reset_index()

df_real.head()'''

"# df_full 2019 12 - predicción vs realidad\n\ndf_real = df_full[(df_full['periodo'] == pd.to_datetime('2019-12-01'))]\n\n# Agregar por product_id\ndf_real = df_real.groupby('product_id')['tn'].sum().reset_index()\n\ndf_real.head()"

In [ ]:
'''# Merge con dataframe por product_id
df_real = pd.merge(df_real, submission_agg2, on='product_id', how='inner')

df_real.head()'''

"# Merge con dataframe por product_id\ndf_real = pd.merge(df_real, submission_agg2, on='product_id', how='inner')\n\ndf_real.head()"

In [ ]:
'''import matplotlib.pyplot as plt


plt.figure(figsize=(8, 6))
plt.scatter(df_real['tn_x'], df_real['tn_y'], alpha=0.6)
plt.plot([df_real['tn_x'].min(), df_real['tn_x'].max()],
         [df_real['tn_x'].min(), df_real['tn_x'].max()],
         'r--', label='Perfecta predicción')
plt.xlabel('Ventas reales (tn) 2019-12')
plt.ylabel('Predicción modelo (tn) 2019-12')
plt.title('Comparación: Real vs Predicción')
plt.legend()
plt.grid(True)
plt.show()'''

"import matplotlib.pyplot as plt\n\n\nplt.figure(figsize=(8, 6))\nplt.scatter(df_real['tn_x'], df_real['tn_y'], alpha=0.6)\nplt.plot([df_real['tn_x'].min(), df_real['tn_x'].max()],\n         [df_real['tn_x'].min(), df_real['tn_x'].max()],\n         'r--', label='Perfecta predicción')\nplt.xlabel('Ventas reales (tn) 2019-12')\nplt.ylabel('Predicción modelo (tn) 2019-12')\nplt.title('Comparación: Real vs Predicción')\nplt.legend()\nplt.grid(True)\nplt.show()"

In [ ]:
'''import plotly.express as px

fig = px.scatter(
    df_real,
    x='tn_x',
    y='tn_y',
    hover_data=['product_id'],
    labels={
        'tn_x': 'Ventas reales (tn) 2019-12',
        'tn_y': 'Predicción modelo (tn) 2019-12'
    },
    title='Comparación: Real vs Predicción (por producto)'
)

# Línea de referencia de predicción perfecta
fig.add_shape(
    type='line',
    x0=df_real['tn_x'].min(), y0=df_real['tn_x'].min(),
    x1=df_real['tn_x'].max(), y1=df_real['tn_x'].max(),
    line=dict(color='red', dash='dash'),
    name='Perfecta predicción'
)

fig.show()'''

"import plotly.express as px\n\nfig = px.scatter(\n    df_real,\n    x='tn_x',\n    y='tn_y',\n    hover_data=['product_id'],\n    labels={\n        'tn_x': 'Ventas reales (tn) 2019-12',\n        'tn_y': 'Predicción modelo (tn) 2019-12'\n    },\n    title='Comparación: Real vs Predicción (por producto)'\n)\n\n# Línea de referencia de predicción perfecta\nfig.add_shape(\n    type='line',\n    x0=df_real['tn_x'].min(), y0=df_real['tn_x'].min(),\n    x1=df_real['tn_x'].max(), y1=df_real['tn_x'].max(),\n    line=dict(color='red', dash='dash'),\n    name='Perfecta predicción'\n)\n\nfig.show()"

In [ ]:
'''
df_real['real-pred'] = df_real['tn_x'] - df_real['tn_y']
df_real['err_abs'] = (df_real['tn_x'] - df_real['tn_y']).abs()
df_real.sort_values(by='tn_y', ascending=False, inplace=True)
df_real.reset_index(drop=True, inplace=True)
df_real.head(20)'''

"\ndf_real['real-pred'] = df_real['tn_x'] - df_real['tn_y']\ndf_real['err_abs'] = (df_real['tn_x'] - df_real['tn_y']).abs()\ndf_real.sort_values(by='tn_y', ascending=False, inplace=True)\ndf_real.reset_index(drop=True, inplace=True)\ndf_real.head(20)"

In [ ]:
'''import plotly.graph_objects as go

# Elige el product_id manualmente
product_id_elegido = 20001  # Cambia este valor por el que quieras analizar

# Agrupa y suma las toneladas por producto y periodo
df_hist = (
    df_full[df_full['product_id'] == product_id_elegido]
    .groupby('periodo', as_index=False)['tn']
    .sum()
    .sort_values('periodo')
)

# Busca la predicción para ese producto
#pred_row = df_real[df_real['product_id'] == product_id_elegido]

fig = go.Figure()

# Línea de evolución histórica
fig.add_trace(go.Scatter(
    x=df_hist['periodo'],
    y=df_hist['tn'],
    mode='lines+markers',
    name='Histórico tn'
))

# Punto de predicción (si existe)
if not pred_row.empty:
    # Ajusta el periodo del punto según corresponda
    periodo_pred = pd.to_datetime('2020-02-01') # df_hist['periodo'].max()
    fig.add_trace(go.Scatter(
        x=[periodo_pred],
        y=pred_row['tn_y'],
        mode='markers',
        marker=dict(color='red', size=12, symbol='star'),
        name='Predicción modelo'
    ))

fig.update_layout(
    title=f'Evolución de tn vendidas y predicción para product_id {product_id_elegido}',
    xaxis_title='Periodo',
    yaxis_title='Toneladas vendidas',
    showlegend=False #,legend=dict(x=0.01, y=0.99)
)
fig.show()'''

"import plotly.graph_objects as go\n\n# Elige el product_id manualmente\nproduct_id_elegido = 20001  # Cambia este valor por el que quieras analizar\n\n# Agrupa y suma las toneladas por producto y periodo\ndf_hist = (\n    df_full[df_full['product_id'] == product_id_elegido]\n    .groupby('periodo', as_index=False)['tn']\n    .sum()\n    .sort_values('periodo')\n)\n\n# Busca la predicción para ese producto\n#pred_row = df_real[df_real['product_id'] == product_id_elegido]\n\nfig = go.Figure()\n\n# Línea de evolución histórica\nfig.add_trace(go.Scatter(\n    x=df_hist['periodo'],\n    y=df_hist['tn'],\n    mode='lines+markers',\n    name='Histórico tn'\n))\n\n# Punto de predicción (si existe)\nif not pred_row.empty:\n    # Ajusta el periodo del punto según corresponda\n    periodo_pred = pd.to_datetime('2020-02-01') # df_hist['periodo'].max()\n    fig.add_trace(go.Scatter(\n        x=[periodo_pred],\n        y=pred_row['tn_y'],\n        mode='markers',\n        marker=dict(color='red', s